<a href="https://colab.research.google.com/github/fur-elyse/clip-and-sub-youtube/blob/main/Generate_Subs_Using_Whisper.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install git+https://github.com/openai/whisper.git
!pip install ffmpeg-python

In [ ]:
import whisper
import ffmpeg
from whisper.utils import write_srt

# import packages for playing audio/video in colab
from base64 import b64encode
from IPython.display import HTML
from IPython.display import Audio


def play_video(filename):
    mp4 = open(filename,'rb').read()
    data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
    return HTML('''
    <video width=400 controls>
        <source src="{data_url}" type="video/mp4">
    </video>
    '''.format(data_url=data_url))

In [ ]:
video = "9CTzhqVHmww.mp4"
subbed_video = video.split(".")[0]+"_subs.mp4"  # output file for subbed video
srt_file = "subtitles.srt"

In [ ]:
# convert video to mp3 file
!ffmpeg -y -i {video} -vn -loglevel error audio.mp3

In [ ]:
# preview the audio
Audio("audio.mp3")

In [ ]:
# load once unless you want to change the language model
# reference: https://github.com/openai/whisper#available-models-and-languages
model = whisper.load_model("large-v2")

# load audio
audio = whisper.load_audio("audio.mp3")

# specify the options
kwargs = {}
kwargs['task'] = "transcribe"
kwargs['language'] = "en"

# decode the audio
result = model.transcribe(audio, **kwargs)

100%|█████████████████████████████████████| 2.87G/2.87G [01:30<00:00, 34.1MiB/s]


In [ ]:
# print the text and verify if it's correct
for res in result["segments"]:
  print(res["text"])

 The term wagyu literally translates to Japanese cow,
 and it generally refers to four main breeds.
 These cows were bred for physical endurance,
 giving them more intramuscular fat cells.


In [ ]:
# save SRT locally and convert into ass and store in drive
with open(srt_file, "w", encoding="utf-8") as srt:
    write_srt(result["segments"], file=srt)

In [ ]:
input_video = ffmpeg.input(video).video
input_audio = ffmpeg.input(video).audio


out = (
    ffmpeg.concat(
        input_video.filter("subtitles", srt_file),
        input_audio,
        v=1, 
        a=1
    )
    .output(
        subbed_video,
        loglevel="error"
    )
)

out.overwrite_output().run()

(None, None)

In [ ]:
play_video(subbed_video)